# Geometrias das faixas de pedestre

In [21]:
import geopandas as gpd
import rasterio
import numpy as np
from sklearn.cluster import DBSCAN
from shapely.geometry import MultiPoint, LineString, Point
from shapely.ops import substring, split, nearest_points
from scipy.spatial import distance
import math
import os
from rasterio.enums import Resampling
import glob
import re

In [22]:
distritos = gpd.read_file(f'downloads/SIRGAS_GPKG_distrito.gpkg')
gdf_scms = gpd.read_file('downloads/SIRGAS_SHP_quadriculaortofoto2017.zip!SIRGAS_SHP_quadriculaortofoto2017/SIRGAS_SHP_quadriculaortofoto2017.shp')

In [24]:
# faixas_list = []
epilson = 6

In [25]:
def quadri_metrics(coords):
    
    distances, angles = [], []

    for i, v in enumerate(coords):
        if i == 0 : continue
        distances.append(distance.euclidean(coords[i-1], v))
        angle_dif = np.array(coords[i-1]) - np.array(v)
        angles.append(math.atan2(angle_dif[0], angle_dif[1]))

    distances = np.array(distances)

    return np.min(distances), np.max(distances), angles[distances.argmin()], angles[distances.argmax()]

    

In [26]:
scms_1000 = distritos.sjoin(gdf_scms, how='right', predicate='intersects')

In [27]:
scms_1000

index_left ds_codigo         ds_subpref ds_cd_sub ds_sigla  \
0           66.0        52        PARELHEIROS        20      MAR   
1           66.0        52        PARELHEIROS        20      MAR   
2           61.0        43        M'BOI MIRIM        18      JDA   
3           61.0        43        M'BOI MIRIM        18      JDA   
3           67.0        55        PARELHEIROS        20      PLH   
...          ...       ...                ...       ...      ...   
4245        67.0        55        PARELHEIROS        20      PLH   
4246        65.0        30  CAPELA DO SOCORRO        19      GRA   
4247        65.0        30  CAPELA DO SOCORRO        19      GRA   
4248        67.0        55        PARELHEIROS        20      PLH   
4249        67.0        55        PARELHEIROS        20      PLH   

            ds_nome qo2010_cod  \
0          MARSILAC     2242-3   
1          MARSILAC     3243-1   
2     JARDIM ANGELA   3335-313   
3     JARDIM ANGELA   2346-434   
3       PARELHEIROS   2346-434   
...             ...        ...   
4245    PARELHEIROS     2222-1   
4246         GRAJAU     3213-4   
4247         GRAJAU     3212-2   
4248    PARELHEIROS     3215-4   
4249    PARELHEIROS     2224-2   

                                               geometry  
0     POLYGON ((315509.362 7353816.286, 315479.774 7...  
1     POLYGON ((334624.805 7351741.359, 334598.259 7...  
2     POLYGON ((321630.403 7373507.865, 321623.309 7...  
3     POLYGON ((321099.428 7373501.324, 321092.313 7...  
3     POLYGON ((321099.428 7373501.324, 321092.313 7...  
...                                                 ...  
4245  POLYGON ((315302.750 7369967.220, 315273.340 7...  
4246  POLYGON ((327567.270 7365503.430, 328097.940 7...  
4247  POLYGON ((331732.130 7372474.840, 334386.680 7...  
4248  POLYGON ((324997.880 7358549.990, 324990.880 7...  
4249  POLYGON ((318545.780 7365393.030, 318516.830 7...  

[5775 rows x 8 columns]

In [32]:
if not os.path.exists(f'resultados/vetor/{folder}'):
    os.makedirs(f'resultados/vetor/{folder}')
    print(f'resultados/vetor/{folder}')

In [76]:
for i, d in distritos.iterrows():

    folder = f'{d.ds_codigo} - {d.ds_nome}'
    
    if not os.path.exists(f'resultados/vetor/{folder}'):
        os.makedirs(f'resultados/vetor/{folder}')
        print(f'resultados/vetor/{folder}')
    else:
        continue

    gdf_pvias = gpd.read_file(f'../poligono-de-vias/resultado/pre-processamentos/{d.ds_codigo}_pre_poligono_de_vias_{d.ds_nome.lower().replace(" ", "_")}.gpkg')
    gdf_rotas_mediais = gpd.read_file(f'../rotas-em-calcadas/resultados/eixos_mediais/{d.ds_codigo}-eixos-mediais-{d.ds_nome}.gpkg')

    gdf_pvias_buffered = gdf_pvias.buffer(-1).unary_union
    gdf_pvias_union = gpd.GeoSeries(gdf_pvias.unary_union)
    
    rasters = [f'resultados/raster/faixas-{scm}.jp2' for scm in scms_1000[scms_1000.ds_codigo == d.ds_codigo]['qo2010_cod']]
    # print(len(rasters), d.ds_nome)

    for f in rasters:
        
        scm = re.findall(r'[0-9]+-[0-9]+', f)[0]

        if os.path.exists(f'resultados/vetor/{folder}/faixas-poly-{scm}.gpkg'):
            continue

        print(f'Processando: SCM {scm}')

        dataset = rasterio.open(f)

        data = dataset.read()
        faixas_ij = np.array([np.where(data == 1)[2], np.where(data == 1)[1]]).transpose()
        t = dataset.transform
        faixas_xy = faixas_ij * (t[0], t[4]) + (t[2], t[5]) + (t[0]/2, t[4]/2)
        # faixas_list.append(faixas_xy)

        geometries = gpd.points_from_xy(x=faixas_xy[:, 0], y=faixas_xy[:, 1], crs='EPSG:31983')
        gdf_faixas = gpd.GeoDataFrame(geometry=geometries)
        
        gdf_faixas = gpd.sjoin(gdf_faixas, gdf_pvias, how='left', predicate='within')
        gdf_faixas.loc[gdf_faixas.index_right.isna(), ['index_right']] = 0
        gdf_faixas.loc[:, ['index_right']] = gdf_faixas.loc[:, ['index_right']] * (epilson + 1) + epilson + 1

        coords = np.array([gdf_faixas.geometry.x, gdf_faixas.geometry.y, gdf_faixas.index_right]).transpose()

        if coords.shape[0] == 0:
            continue

        clusters = DBSCAN(eps=epilson).fit_predict(coords)
        
        gdf_faixas.loc[:, ['cluster']] = clusters

        # Remove ruido dos clusters
        gdf_faixas = gdf_faixas[gdf_faixas.cluster != -1]

        # gdf_faixas.to_file(f'resultados/vetor/faixas-{scm}.gpkg', driver='GPKG')

        faixas_poly = gdf_faixas.groupby('cluster')['geometry'].apply(lambda x: MultiPoint(list(x)).minimum_rotated_rectangle)
        
        # Remove polígonos com área menor que 2m
        faixas_poly = faixas_poly[faixas_poly.geometry.area > 2]

        # faixas_poly.to_file(f'resultados/vetor/faixas-{scm}.gpkg', driver='GPKG')

        # Remove os polígonos que o ponto de inacessibilidade esteja 
        # fora de um buffer negativo de 1m do polígono de via
        faixas_poly = faixas_poly[faixas_poly.geometry.apply(lambda x: x.representative_point()).intersects(gdf_pvias_buffered)]

        # faixas_poly[:, ['largura', 'extensão', 'angulo da largura', 'angulo da extensão']] = \
        #     quadri_metrics()

        faixas_poly = gpd.GeoDataFrame(faixas_poly.geometry.exterior.apply(lambda x: quadri_metrics(x.coords)).to_list(), 
                                        index=faixas_poly.index, 
                                        geometry=faixas_poly.geometry, 
                                        columns=['largura', 'extensão', 'angulo da largura', 'angulo da extensão'])

        # 1. Encontrar a rota medial mais próxima
        medial_proxima = faixas_poly.sjoin_nearest(gdf_rotas_mediais, how='left', max_distance=80.0, distance_col='distancia')
        # Removendo duplicados
        medial_proxima = medial_proxima[~medial_proxima.index.duplicated(keep='first')]
        # Removendo sem associação
        medial_proxima = medial_proxima[medial_proxima.index_right.notna()]

        # 2. Obter os pontos entre a rota medial e o polígono
        linha_conexao_1 = medial_proxima.apply(lambda x: LineString(nearest_points(gdf_rotas_mediais.iloc[int(x.index_right)].geometry,x.geometry)), axis=1)

        if len(linha_conexao_1) == 0:
            print('vazio!')
            continue

        # 3. Obter o ponto invertido dentro do polígono
        faixas_poly = faixas_poly.loc[linha_conexao_1.index] # para garantir a relação com o DF linha_conexao
        faixas_poly.loc[:, ['pt_invertido_norm']] = faixas_poly.apply(lambda x: x.geometry.boundary.project(Point(linha_conexao_1[x.name].coords[0]), normalized=True), axis=1)
        faixas_poly.loc[:, ['pt_invertido_norm']] += 0.5
        
        faixas_poly.loc[faixas_poly.pt_invertido_norm > 1.0, 'pt_invertido_norm'] -= 1.0

        # try:
        pt_2 = gpd.GeoDataFrame(geometry=faixas_poly.apply(lambda x: x.geometry.boundary.interpolate(x.pt_invertido_norm, normalized=True), axis=1))
        # except:
        #     pt_2 = gpd.GeoDataFrame(geometry=[])
        
        # 4. Conectar o ponto invertido do polígono às rotas mediais unificadas
        medial_proxima = pt_2.sjoin_nearest(gdf_rotas_mediais, how='left', max_distance=80.0, distance_col='distancia')
        # Removendo duplicados
        medial_proxima = medial_proxima[~medial_proxima.index.duplicated(keep='first')]
        # Removendo sem associação
        medial_proxima = medial_proxima[medial_proxima.index_right.notna()]

        linha_conexao_2 = medial_proxima.apply(lambda x: LineString(nearest_points(x.geometry,
                                                                                    gdf_rotas_mediais.iloc[int(x.index_right)].geometry,)), axis=1)
                                                                                    
        # 5. Desenhar a linha entre todos os pontos
        pt_1 = linha_conexao_1.apply(lambda x: x.coords[0]).to_numpy()
        pt_2 = linha_conexao_2.apply(lambda x: x.coords[1]).to_numpy()

        if pt_1.shape != pt_2.shape:
            continue

        # try:
        linhas_de_travessia = gpd.GeoDataFrame(geometry=[LineString([x[0], x[1]]) for x in np.stack([pt_1, pt_2], axis=-1)])
        linhas_de_travessia.to_file(f'resultados/vetor/{folder}/linhas-de-travessia-{scm}.gpkg', driver='GPKG')

        # 6. Gerar um offset com a largura da faixa a partir da linha de travessia
        travessia_buffered = gpd.GeoDataFrame(geometry=linhas_de_travessia.apply(lambda x: 
                                x.geometry.buffer(faixas_poly.reset_index().largura[x.name]/2, cap_style=3), axis=1))
        
        # 7. Cortar o novo polígono para ficar contido no polígono de vias                                
        travessia_buffered = gpd.clip(travessia_buffered, gdf_pvias_union)
        if len(travessia_buffered) > 0:
            travessia_buffered.to_file(f'resultados/vetor/{folder}/faixas-poly-{scm}.gpkg', driver='GPKG')
            
        # except:
        #     print('vazio')

        # faixas_poly.to_file(f'resultados/vetor/faixas-poly-{scm}.gpkg', driver='GPKG')
        # gdf_faixas.plot()

        # break



resultados/vetor/11 - BRASILANDIA
Processando: SCM 3432-344


/home/feromes/miniconda3/envs/geo/lib/python3.8/site-packages/geopandas/geodataframe.py:2050: UserWarning: CRS mismatch between the CRS of left geometries and the CRS of right geometries.
Use `to_crs()` to reproject one of the input geometries to match the CRS of the other.

Left CRS: None
Right CRS: EPSG:31983

  return geopandas.sjoin_nearest(


vazio!
Processando: SCM 3434-121


/home/feromes/miniconda3/envs/geo/lib/python3.8/site-packages/geopandas/geodataframe.py:2050: UserWarning: CRS mismatch between the CRS of left geometries and the CRS of right geometries.
Use `to_crs()` to reproject one of the input geometries to match the CRS of the other.

Left CRS: None
Right CRS: EPSG:31983

  return geopandas.sjoin_nearest(


vazio!
Processando: SCM 3434-112
Processando: SCM 3434-111


...

/home/feromes/miniconda3/envs/geo/lib/python3.8/site-packages/geopandas/geodataframe.py:2050: UserWarning: CRS mismatch between the CRS of left geometries and the CRS of right geometries.
Use `to_crs()` to reproject one of the input geometries to match the CRS of the other.

Left CRS: None
Right CRS: EPSG:31983

  return geopandas.sjoin_nearest(
/home/feromes/miniconda3/envs/geo/lib/python3.8/site-packages/geopandas/geodataframe.py:2050: UserWarning: CRS mismatch between the CRS of left geometries and the CRS of right geometries.
Use `to_crs()` to reproject one of the input geometries to match the CRS of the other.

Left CRS: None
Right CRS: EPSG:31983

  return geopandas.sjoin_nearest(
/home/feromes/miniconda3/envs/geo/lib/python3.8/site-packages/geopandas/io/file.py:362: FutureWarning: pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.
  pd.Int64Index,
/home/feromes/miniconda3/envs/geo/lib/python3.

Processando: SCM 4313-251


/home/feromes/miniconda3/envs/geo/lib/python3.8/site-packages/geopandas/geodataframe.py:2050: UserWarning: CRS mismatch between the CRS of left geometries and the CRS of right geometries.
Use `to_crs()` to reproject one of the input geometries to match the CRS of the other.

Left CRS: None
Right CRS: EPSG:31983

  return geopandas.sjoin_nearest(
/home/feromes/miniconda3/envs/geo/lib/python3.8/site-packages/geopandas/geodataframe.py:2050: UserWarning: CRS mismatch between the CRS of left geometries and the CRS of right geometries.
Use `to_crs()` to reproject one of the input geometries to match the CRS of the other.

Left CRS: None
Right CRS: EPSG:31983

  return geopandas.sjoin_nearest(
/home/feromes/miniconda3/envs/geo/lib/python3.8/site-packages/geopandas/io/file.py:362: FutureWarning: pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.
  pd.Int64Index,
/home/feromes/miniconda3/envs/geo/lib/python3.

Processando: SCM 4313-242
vazio!


/home/feromes/miniconda3/envs/geo/lib/python3.8/site-packages/geopandas/geodataframe.py:2050: UserWarning: CRS mismatch between the CRS of left geometries and the CRS of right geometries.
Use `to_crs()` to reproject one of the input geometries to match the CRS of the other.

Left CRS: None
Right CRS: EPSG:31983

  return geopandas.sjoin_nearest(


In [73]:
pt_2

geometry
cluster                                
3        POINT (328410.894 7405921.022)
4        POINT (328382.094 7405915.262)
5        POINT (328434.951 7405905.303)
6        POINT (328460.214 7405900.862)